In [1]:
from openai import OpenAI
from dotenv import load_dotenv 
import glob
import json
import os
import time
from pydantic import BaseModel
from openai import BadRequestError
import pandas as pd
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
from tqdm import tqdm

# 加载环境变量
load_dotenv() 

# 创建OpenAI客户端
client = OpenAI(base_url=os.getenv("BAILIAN_API_BASE_URL"),
       api_key=os.getenv("BAILIAN_API_KEY"))
DATA_ROOT = "D:/ai_learning-master/ai_learning/data/acllmdb_sentiment_small"
SAVE_PATH = "./prediction_results.csv"

class SentimentRequest(BaseModel):
    sentiment: str




In [ ]:
def load_dataset():
    """加载数据集并返回带标签的样本列表"""
    samples = []
    for label in ["positive", "negative"]:
        dir_path = os.path.join(DATA_ROOT, label)
        for file_path in glob.glob(os.path.join(dir_path, "*.txt")):
            with open(file_path, "r", encoding="utf-8") as f:
                samples.append({
                    "text": f.read(),
                    "true_label": label
                })
    return samples

In [5]:
def predict_text(client, text, max_retries=3):
    """纯文本模式预测"""
    prompt = f"""请判断以下影评的情感倾向，严格只输出英文单词positive或negative：
{text}"""
    
    for _ in range(max_retries):
        try:
            response = client.chat.completions.create(
                model="qwen3-4b",
                messages=[{"role": "user", "content": prompt}],
                temperature=0,
                extra_body={"enable_thinking": False}
            )
         
            return response.choices[0].message.content.strip().lower()
        except BadRequestError:
            time.sleep(1)
    return "error"

def predict_json(client, text, max_retries=3):
    """JSON模式预测"""
    prompt = f"""分析以下影评的情感倾向，使用JSON格式返回结果：
{text}"""
    
    for _ in range(max_retries):
        try:
            response = client.chat.completions.create(
                model="qwen3-4b",
                messages=[{"role": "user", "content": prompt}],
                response_format={"type": "json_object"},
                temperature=0,
                extra_body={"enable_thinking": False}
            )
            result = json.loads(response.choices[0].message.content)
            return SentimentRequest(**result).sentiment
        except:
            time.sleep(1)
    return "error"

def predict_tool(client, text, max_retries=3):
    """工具调用模式预测"""
    prompt = f"""请分析以下影评的情感倾向：
{text}"""
    
    tools = [{
        "type": "function",
        "function": {
            "name": "sentiment_analysis",
            "description": "情感分析结果",
            "parameters": {
                "type": "object",
                "properties": {
                    "sentiment": {
                        "type": "string", 
                        "enum": ["positive", "negative"],
                        "description": "情感倾向"
                    }
                },
                "required": ["sentiment"]
            }
        }
    }]
    
    for _ in range(max_retries):
        try:
            response = client.chat.completions.create(
                model="qwen3-4b",
                messages=[{"role": "user", "content": prompt}],
                tools=tools,
                tool_choice={"type": "function", "function": {"name": "sentiment_analysis"}},
                temperature=0,
                extra_body={"enable_thinking": False}
            )
            args = json.loads(response.choices[0].message.tool_calls[0].function.arguments)
            return SentimentRequest(**args).sentiment
        except:
            time.sleep(1)
    return "error"


In [6]:
def main():
    # 初始化客户端
    client = OpenAI(
        base_url=os.getenv("BAILIAN_API_BASE_URL"),
        api_key=os.getenv("BAILIAN_API_KEY")
    )
    
    # 加载数据
    samples = load_dataset()
    print(f"成功加载 {len(samples)} 条样本")
    
    # 执行预测
    results = []
    for sample in tqdm(samples, desc="预测进度"):
        try:
            pred_text = predict_text(client, sample["text"])
            pred_json = predict_json(client, sample["text"])
            pred_tool = predict_tool(client, sample["text"])
            
            results.append({
                "text": sample["text"],
                "true_label": sample["true_label"],
                "text_pred": pred_text,
                "json_pred": pred_json,
                "tool_pred": pred_tool
            })
        except Exception as e:
            print(f"预测失败：{str(e)}")
    
    # 保存结果
    df = pd.DataFrame(results)
    df.to_csv(SAVE_PATH, index=False)
    print(f"预测结果已保存至：{SAVE_PATH}")
    
    # 计算指标
    for mode in ["text_pred","json_pred","tool_pred"]:
        y_true = df["true_label"]
        y_pred = df[mode]
        accuracy = accuracy_score(y_true, y_pred)
        print(f"{mode.split('_')[0]}模式准确率：{accuracy:.2%}")
if __name__ == "__main__":
    main()

成功加载 21 条样本


预测进度: 100%|██████████| 21/21 [00:57<00:00,  2.72s/it]

预测结果已保存至：./prediction_results.csv
text模式准确率：90.48%
json模式准确率：90.48%
tool模式准确率：85.71%


In [ ]:
# 新单元格1：定义独立函数
from tqdm.notebook import tqdm
from openai import OpenAI
import pandas as pd

def compare_models():
    """独立模型比较函数"""
    # 初始化独立客户端
    local_client = OpenAI(
        base_url=os.getenv("BAILIAN_API_BASE_URL"),
        api_key=os.getenv("BAILIAN_API_KEY")
    )
    
    # 独立模型列表
    MODEL_COMPARE = [
        "qwen3-32b",
        "qwen3-30b-a3b",
        "qwen3-0.6b"
    ]
    
    def local_predict(text, model_name, max_retries=3):
        """独立预测函数"""
        prompt = f"判断情感倾向（仅输出positive/negative）：\n{text}"
        for _ in range(max_retries):
            try:
                response = local_client.chat.completions.create(
                    model=model_name,
                    messages=[{"role": "user", "content": prompt}],
                    temperature=0,
                    extra_body={"enable_thinking": False}
                )
                return response.choices[0].message.content.strip().lower()
            except Exception:
                time.sleep(1)
        return "error"
    
    # 独立数据加载
    local_samples = load_dataset()  # 复用已有加载函数
    
    # 执行比较
    report = []
    for model in MODEL_COMPARE:
        correct = 0
        for sample in tqdm(local_samples, desc=f"Testing {model}"):
            pred = local_predict(sample["text"], model)
            if pred == sample["true_label"]:
                correct += 1
        report.append({
            "Model": model,
            "Accuracy": f"{correct/len(local_samples):.2%}",
            "Params": model.split("-")[1].upper()
        })
    
    # 显示结果
    return pd.DataFrame(report)

In [12]:
result_df = compare_models()
result_df.style.hide(axis="index").format(precision=2)

Testing qwen3-32b:   0%|          | 0/21 [00:00<?, ?it/s]

Testing qwen3-30b-a3b:   0%|          | 0/21 [00:00<?, ?it/s]

Testing qwen3-0.6b:   0%|          | 0/21 [00:00<?, ?it/s]

In [32]:
def analyze_with_reason():
    """使用qwen3-0.6b进行带原因的情感分析"""
    client = OpenAI(
        base_url=os.getenv("BAILIAN_API_BASE_URL"),
        api_key=os.getenv("BAILIAN_API_KEY")
    )
    
    # 自定义工具定义
    tools = [{
        "type": "function",
        "function": {
            "name": "sentiment_analysis",
            "description": "情感分析结果及原因",
            "parameters": {
                "type": "object",
                "properties": {
                    "sentiment": {
                        "type": "string", 
                        "enum": ["positive", "negative"],
                        "description": "情感倾向"
                    },
                    "reason": {
                        "type": "string",
                        "description": "分析原因"
                    }
                },
                "required": ["sentiment", "reason"]
            }
        }
    }]
    
    # 加载数据
    samples = load_dataset()
    error_cases = []
    
    for sample in tqdm(samples, desc="分析进度"):
        try:
            # 工具调用预测
            response = client.chat.completions.create(
                model="qwen3-0.6b",
                messages=[{
                    "role": "user", 
                    "content": f"请分析以下影评情感并说明原因：\n{sample['text']}"
                }],
                tools=tools,
                tool_choice={"type": "function", "function": {"name": "sentiment_analysis"}},
                temperature=0,
                extra_body={"enable_thinking": False}
            )
            
            # 解析结果
            args = json.loads(response.choices[0].message.tool_calls[0].function.arguments)
            pred = args["sentiment"]
            reason = args["reason"]
            
            # 记录错误案例
            if pred != sample["true_label"]:
                error_cases.append({
                    "text": sample["text"],
                    "true_label": sample["true_label"],
                    "prediction": pred,
                    "reason": reason
                })
                
        except Exception as e:
            print(f"分析失败：{str(e)}")
            continue
    
    # 保存错误案例
    error_df = pd.DataFrame(error_cases)
    error_df.to_csv("./error_analysis.csv", index=False)
    return error_df


In [33]:
error_results = analyze_with_reason()
print(f"发现 {len(error_results)} 个错误案例")
error_results.head()

分析进度:   0%|          | 0/21 [00:00<?, ?it/s]

分析失败：'sentiment'
发现 4 个错误案例


text true_label prediction  \
0  How many movies are there that you can think o...   positive   negative   
1  I only went to see this movie because I have a...   positive   negative   
2  I'm a Petty Officer 1st Class (E-6) and have b...   positive   negative   
3  Wow, another Kevin Costner hero movie. Postman...   negative   positive   

                                              reason  
0  The movie borrows so much from other movies, l...  
1  The movie missed some acting moments, scenes w...  
2  The movie portrayed the Coast Guard in a way t...  
3  The review highlights Kevin Costner's consiste...

In [ ]:
#修改temperature查看结果,从0修改至1.9
error_results = analyze_with_reason()
print(f"发现 {len(error_results)} 个错误案例")
error_results.head()

分析进度:   0%|          | 0/21 [00:00<?, ?it/s]

发现 5 个错误案例


text true_label prediction  \
0  How many movies are there that you can think o...   positive   negative   
1  I only went to see this movie because I have a...   positive   negative   
2  I'm a Petty Officer 1st Class (E-6) and have b...   positive   negative   
3  I've seen this story before but my kids haven'...   positive      mixed   
4  Wow, another Kevin Costner hero movie. Postman...   negative   positive   

                                              reason  
0  Borrowing so much from multiple movies creates...  
1  Although some aspects of the movie have positi...  
2                         The sentiment is negative.  
3  the review contains both positive and negative...  
4  the movie is highlighted by its relatability, ...